In [2]:
import pandas as pd
import numpy as np
import sys
import os
import gc
from loguru import logger
from tqdm import tqdm

sys.path.append("../../../../note")
sys.path.append(os.getcwd())

%load_ext autoreload
%autoreload 2

from module.get_info_FinMind import FinMindClient
from module.get_info_Postgre import PostgreClient
pg = PostgreClient('windows', database='stock_daily')
from module.options.option_tools import compute_iv

from analyzer import TXAnalyzer

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# get data

In [3]:
START = "2010-01-01"
END = "2026-01-20"

fm = FinMindClient()
fm.initialize_frame(stock_id="TX", start_time=START, end_time=END)
analyzer = TXAnalyzer(fm.get_future_price())
margin_df = fm.get_total_margin_info()
margin_df.to_csv('../../../data/margin_info.csv')

margin_maintenance = fm.get_total_margin_maintenance(start_time=START, end_time=END)
margin_info = pg.fetch_table('total_margin_info')

2026-02-03 16:31:32.736 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanFuturesDaily, data_id: TX
2026-02-03 16:31:52.360 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanStockTotalMarginPurchaseShortSale, data_id: 
2026-02-03 16:31:53.367 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanTotalExchangeMarginMaintenance, data_id: 


# analysis

## 日盤跟夜盤分開的 dilay ret & 月報酬
### `漲都是夜盤在漲，日盤上上下下不太明顯`
### 但 2、4 月可以日盤當沖

In [232]:
analyzer.daily_ret()
analyzer.monthly_ret(mode='benchmark')
analyzer.monthly_ret(mode='strategy')

In [116]:
analyzer.indicator_weekday_stats()

=== Weekday Average Returns ===


daily_ret  daily_ret_a
weekday                        
Mon       0.000373     0.000229
Tue       0.000102     0.000638
Wed       0.000426     0.000615
Thu      -0.000224     0.000948
Fri      -0.000133     0.000428
Sat       0.000184    -0.000544

## `Price`
日盤  
night_price < 0.012 & > 0.0094 以外，可以用 0 去切，有正向關係

In [17]:
analyzer.indicator_15ma_divergence()

In [85]:
analyzer.indicator_night_price()
analyzer.indicator_night_price(sub_analysis=True)

KeyError: 'cum_demeaned_daily_ret'

## 價差

In [16]:
analyzer.indicator_spread()

## `放假天數`
放長假前會下跌  
放長假後會比較晃，只是總體而言是上漲

In [137]:
analyzer.indicator_gap_days(after_holiday=False)
analyzer.indicator_gap_days(after_holiday=True)

In [239]:
analyzer.indicator_gap_days(after_holiday=True, sub_analysis=True)

## `大盤融資維持率`
適合超底??

155 前可以 allin，但後面就沒傾向了  
但每個券商、資料商的資料算法不一定一樣

In [151]:
temp_df = analyzer.display_df()
temp_df = temp_df.reset_index(names='date')
margin_maintenance['date'] = pd.to_datetime(margin_maintenance['date'])
temp_df = temp_df.merge(margin_maintenance, how='left', on='date')
temp_df.set_index('date', inplace=True)
analyzer.update_df(temp_df)

futures_id contract_date monthly_group     Open     High      Low  \
date                                                                           
2020-01-02         TX        202001    2020-01-15  12044.0  12120.0  12023.0   
2020-01-03         TX        202001    2020-01-15  12180.0  12198.0  11996.0   
2020-01-06         TX        202001    2020-01-15  12017.0  12034.0  11948.0   
2020-01-07         TX        202001    2020-01-15  11995.0  12009.0  11816.0   
2020-01-08         TX        202001    2020-01-15  11728.0  11892.0  11697.0   
...               ...           ...           ...      ...      ...      ...   
2026-01-14         TX        202601    2026-01-21  31000.0  31162.0  30937.0   
2026-01-15         TX        202601    2026-01-21  30831.0  31057.0  30744.0   
2026-01-16         TX        202601    2026-01-21  31382.0  31536.0  31157.0   
2026-01-19         TX        202601    2026-01-21  31272.0  31774.0  31208.0   
2026-01-20         TX        202601    2026-01-21  31481.0  31742.0  31328.0   

              Close  spread  spread_per    Volume  ...  Volume_a  \
date                                               ...             
2020-01-02  12102.0   108.0        0.90  100401.0  ...   22506.0   
2020-01-03  12086.0   -15.0       -0.12  172660.0  ...   32214.0   
2020-01-06  11950.0  -137.0       -1.13  118380.0  ...   36868.0   
2020-01-07  11871.0   -78.0       -0.65  157264.0  ...   38896.0   
2020-01-08  11788.0   -83.0       -0.70  158971.0  ...   36974.0   
...             ...     ...         ...       ...  ...       ...   
2026-01-14  30982.0   112.0        0.36   54974.0  ...   52649.0   
2026-01-15  31050.0    70.0        0.23   58154.0  ...   52310.0   
2026-01-16  31474.0   424.0        1.37   72871.0  ...   65948.0   
2026-01-19  31669.0   193.0        0.61   89177.0  ...   35778.0   
2026-01-20  31672.0     0.0        0.00   81251.0  ...   24067.0   

            settlement_price_a open_interest_a trading_session_a daily_ret  \
date                                                                         
2020-01-02                 0.0             0.0      after_market  0.004816   
2020-01-03                 0.0             0.0      after_market -0.007718   
2020-01-06                 0.0             0.0      after_market -0.005575   
2020-01-07                 0.0             0.0      after_market -0.010338   
2020-01-08                 0.0             0.0      after_market  0.005116   
...                        ...             ...               ...       ...   
2026-01-14                 0.0             0.0      after_market -0.000581   
2026-01-15                 0.0             0.0      after_market  0.007103   
2026-01-16                 0.0             0.0      after_market  0.002932   
2026-01-19                 0.0             0.0      after_market  0.012695   
2026-01-20                 0.0             0.0      after_market  0.006067   

           cum_daily_ret  daily_ret_a  cum_daily_ret_a  US_bond_5y  \
date                                                                 
2020-01-02      0.004816     0.002334         0.002334        1.67   
2020-01-03     -0.002902     0.006034         0.008368        1.59   
2020-01-06     -0.008477    -0.004052         0.004315        1.61   
2020-01-07     -0.018815     0.003183         0.007499        1.62   
2020-01-08     -0.013699     0.003455         0.010953        1.67   
...                  ...          ...              ...         ...   
2026-01-14      0.086057     0.002786         0.788606        3.72   
2026-01-15      0.093160    -0.003200         0.785407        3.77   
2026-01-16      0.096092     0.004907         0.790313        3.82   
2026-01-19      0.108787    -0.004732         0.785582         NaN   
2026-01-20      0.114854    -0.002623         0.782959        3.86   

            TotalExchangeMarginMaintenance  
date                                        
2020-01-02                         166.764  
2020-01-03              

In [152]:
analyzer.indicator_maintenance_rate(point_version=False)

## 融資

In [9]:
temp_df = analyzer.display_df()
temp_df = temp_df.reset_index(names='date')
margin_tf = margin_df.pivot_table(index='date', columns='name', values='TodayBalance')
margin_tf.reset_index(inplace=True)
margin_tf['date'] = pd.to_datetime(margin_tf['date'])
temp_df = temp_df.merge(margin_tf, how='left', on='date')
temp_df.set_index('date', inplace=True)
analyzer.update_df(temp_df)
analyzer.display_df()

futures_id contract_date monthly_group     Open     High      Low  \
date                                                                           
2020-01-02         TX        202001    2020-01-15  12044.0  12120.0  12023.0   
2020-01-03         TX        202001    2020-01-15  12180.0  12198.0  11996.0   
2020-01-06         TX        202001    2020-01-15  12017.0  12034.0  11948.0   
2020-01-07         TX        202001    2020-01-15  11995.0  12009.0  11816.0   
2020-01-08         TX        202001    2020-01-15  11728.0  11892.0  11697.0   
...               ...           ...           ...      ...      ...      ...   
2026-01-14         TX        202601    2026-01-21  31000.0  31162.0  30937.0   
2026-01-15         TX        202601    2026-01-21  30831.0  31057.0  30744.0   
2026-01-16         TX        202601    2026-01-21  31382.0  31536.0  31157.0   
2026-01-19         TX        202601    2026-01-21  31272.0  31774.0  31208.0   
2026-01-20         TX        202601    2026-01-21  31481.0  31742.0  31328.0   

              Close  spread  spread_per    Volume  ...  open_interest_a  \
date                                               ...                    
2020-01-02  12102.0   108.0        0.90  100401.0  ...              0.0   
2020-01-03  12086.0   -15.0       -0.12  172660.0  ...              0.0   
2020-01-06  11950.0  -137.0       -1.13  118380.0  ...              0.0   
2020-01-07  11871.0   -78.0       -0.65  157264.0  ...              0.0   
2020-01-08  11788.0   -83.0       -0.70  158971.0  ...              0.0   
...             ...     ...         ...       ...  ...              ...   
2026-01-14  30982.0   112.0        0.36   54974.0  ...              0.0   
2026-01-15  31050.0    70.0        0.23   58154.0  ...              0.0   
2026-01-16  31474.0   424.0        1.37   72871.0  ...              0.0   
2026-01-19  31669.0   193.0        0.61   89177.0  ...              0.0   
2026-01-20  31672.0     0.0        0.00   81251.0  ...              0.0   

            trading_session_a daily_ret cum_daily_ret daily_ret_a  \
date                                                                
2020-01-02       after_market  0.004816      0.004816    0.002334   
2020-01-03       after_market -0.007718     -0.002902    0.006034   
2020-01-06       after_market -0.005575     -0.008477   -0.004052   
2020-01-07       after_market -0.010338     -0.018815    0.003183   
2020-01-08       after_market  0.005116     -0.013699    0.003455   
...                       ...       ...           ...         ...   
2026-01-14       after_market -0.000581      0.086057    0.002786   
2026-01-15       after_market  0.007103      0.093160   -0.003200   
2026-01-16       after_market  0.002932      0.096092    0.004907   
2026-01-19       after_market  0.012695      0.108787   -0.004732   
2026-01-20       after_market  0.006067      0.114854   -0.002623   

           cum_daily_ret_a  TotalExchangeMarginMaintenance  MarginPurchase  \
date                                                                         
2020-01-02        0.002334                         166.764       7344427.0   
2020-01-03        0.008368                         165.209       7322773.0   
2020-01-06        0.004315                         163.083       7338109.0   
2020-01-07        0.007499                         160.375       7314998.0   
2020-01-08        0.010953                         159.042       7297808.0   
...                    ...                             ...             ...   
2026-01-14        0.788606                         174.515       8040168.0   
2026-01-15        0.785407                         173.912       8045393.0   
2026-01-16        0.790313                         176.183       8129811.0   
2026-01-19        0.785582                         178.775       8245019.0   
2026-01-20        0.782959                         178.747       8214287.0   

            MarginPurchaseMoney  ShortSale  
date                                

In [10]:
analyzer.indicator_margin_delta()

## `選擇權`

### IV

In [121]:
data_chunks = []

# 轉換日期
s_dt = pd.Timestamp(START)
e_dt = pd.Timestamp(END)

# 產生每年的起始時間點作為迴圈依據 (freq='AS' 代表 Year Begin)
# 這樣會產生如 [2010-01-01, 2011-01-01, ...] 的序列
dates = pd.date_range(start=s_dt, end=e_dt, freq='AS')

# 確保起始日有被包含進去 (如果 START 不是 1/1)
if s_dt not in dates:
    dates = dates.insert(0, s_dt)
    dates = dates.sort_values().unique()

# 使用 for 迴圈迭代每一個年份開頭
for current_start in tqdm(dates):
    # 設定該批次的結束時間：推算到該年的 12/31
    current_end = current_start + pd.offsets.YearEnd(0)
    
    # 邊界檢查：如果該年 12/31 超過了我們設定的總結束日(END)，就截斷在 END
    if current_end > e_dt:
        current_end = e_dt
        
    # 確保開始時間小於等於結束時間
    if current_start > current_end:
        continue

    try:
        # 下載該區段資料
        df_part = fm.get_option_daily(
            option_id='TXO',
            start_date=current_start,
            end_date=current_end,
            trading_session='all'
        )
        
        # 只有當有資料時才加入 list
        if not df_part.empty:
            data_chunks.append(df_part)
            
        # 稍微暫停，避免對伺服器請求過快
        time.sleep(0.5)
        
    except Exception as e:
        print(f"下載失敗: {current_start.date()} ~ {current_end.date()}, 原因: {e}")

# 最後合併在一起
if data_chunks:
    opt_df = pd.concat(data_chunks, ignore_index=True)
    print(f"全部下載完成，總筆數: {len(opt_df)}")
else:
    opt_df = pd.DataFrame()
    print("未下載到任何資料")

df = analyzer.display_df()

if not isinstance(df.index, pd.DatetimeIndex):
    df.index = pd.to_datetime(df.index)

spot_df = df[['Close', 'Close_a']].copy()

if not isinstance(opt_df['date'], pd.DatetimeIndex):
    opt_df['date'] = pd.to_datetime(opt_df['date'])

opt_df = opt_df.merge(spot_df, left_on='date', right_index=True, how='left')

opt_df['underlying_price'] = np.where(
    opt_df['trading_session'] == 'after_market', 
    opt_df['Close_a'],
    opt_df['Close']
)

settle_df = pd.read_csv(r"../../../../note/data/settle_TXO.csv")
settle_df["settle_date"] = pd.to_datetime(settle_df["settle_date"])

iv_df = compute_iv(
    opt_df, 
    model="bs", 
    underlying_col="underlying_price", 
    risk_free_rate=0.015,
    shape_options={
        "group_cols": ["date", "contract_date", "trading_session"]
    },
    
    settlement_df = settle_df,
    settlement_contract_col = "contract",
    settlement_date_col = "settle_date"
)

skew_data = iv_df.groupby(['date', 'trading_session'])[['SkewSlope', 'SkewSlope3']].first().reset_index()

skew_pivot = skew_data.pivot(index='date', columns='trading_session', values=['SkewSlope', 'SkewSlope3'])

new_columns = []
for col_name, session in skew_pivot.columns:
    if session == 'position':
        new_columns.append(col_name) # 日盤維持原名
    else:
        new_columns.append(f"{col_name}_a") # 夜盤加 _a

skew_pivot.columns = new_columns
skew_pivot = skew_pivot.reset_index()

skew_pivot['date'] = pd.to_datetime(skew_pivot['date'])

skew_pivot_indexed = skew_pivot.set_index('date')
df = pd.merge(df, skew_pivot_indexed, left_index=True, right_index=True, how='left')

analyzer.update_df(df)

C:\Users\ownme\AppData\Local\Temp\ipykernel_10892\524170086.py:9: FutureWarning:

'AS' is deprecated and will be removed in a future version, please use 'YS' instead.

  6%|▌         | 1/17 [00:10<02:40, 10.06s/it]2026-02-02 20:42:15.841 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanOptionDaily, data_id: TXO


下載失敗: 2010-01-01 ~ 2010-12-31, 原因: name 'time' is not defined


 12%|█▏        | 2/17 [00:28<03:45, 15.06s/it]2026-02-02 20:42:34.399 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanOptionDaily, data_id: TXO


下載失敗: 2011-01-01 ~ 2011-12-31, 原因: name 'time' is not defined


 18%|█▊        | 3/17 [00:31<02:12,  9.49s/it]2026-02-02 20:42:37.257 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanOptionDaily, data_id: TXO


...

100%|██████████| 17/17 [02:32<00:00,  8.97s/it]

下載失敗: 2026-01-01 ~ 2026-01-20, 原因: name 'time' is not defined


全部下載完成，總筆數: 617574


d:\Github\Quant\projects\workStrategy\TX\../../../../note\module\options\iv\iv_shape.py:75: FutureWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



futures_id contract_date monthly_group     Open     High      Low  \
date                                                                           
2010-01-04         TX        201001    2010-01-20   8203.0   8211.0   8101.0   
2010-01-05         TX        201001    2010-01-20   8212.0   8260.0   8125.0   
2010-01-06         TX        201001    2010-01-20   8197.0   8336.0   8179.0   
2010-01-07         TX        201001    2010-01-20   8335.0   8355.0   8230.0   
2010-01-08         TX        201001    2010-01-20   8287.0   8297.0   8183.0   
...               ...           ...           ...      ...      ...      ...   
2026-01-14         TX        202601    2026-01-21  31000.0  31162.0  30937.0   
2026-01-15         TX        202601    2026-01-21  30831.0  31057.0  30744.0   
2026-01-16         TX        202601    2026-01-21  31382.0  31536.0  31157.0   
2026-01-19         TX        202601    2026-01-21  31272.0  31774.0  31208.0   
2026-01-20         TX        202601    2026-01-21  31481.0  31742.0  31328.0   

              Close  spread  spread_per    Volume  ...  cum_daily_pnl_a  \
date                                               ...                    
2010-01-04   8166.0   -35.0       -0.43   84131.0  ...              NaN   
2010-01-05   8178.0    11.0        0.13  108012.0  ...              NaN   
2010-01-06   8320.0   142.0        1.74  120081.0  ...              NaN   
2010-01-07   8259.0   -62.0       -0.75  120555.0  ...              NaN   
2010-01-08   8278.0    18.0        0.22  104771.0  ...              NaN   
...             ...     ...         ...       ...  ...              ...   
2026-01-14  30982.0   112.0        0.36   54974.0  ...          14812.0   
2026-01-15  31050.0    70.0        0.23   58154.0  ...          14713.0   
2026-01-16  31474.0   424.0        1.37   72871.0  ...          14866.0   
2026-01-19  31669.0   193.0        0.61   89177.0  ...          14717.0   
2026-01-20  31672.0     0.0        0.00   81251.0  ...          14634.0   

            Foreign_Opt_Signal Dealer_Opt_Signal Foreign_Opt_Signal_a  \
date                                                                    
2010-01-04                 NaN               NaN                  NaN   
2010-01-05                 NaN               NaN                  NaN   
2010-01-06                 NaN               NaN                  NaN   
2010-01-07                 NaN               NaN                  NaN   
2010-01-08                 NaN               NaN                  NaN   
...                        ...               ...                  ...   
2026-01-14            0.009633         -0.012854             0.006912   
2026-01-15            0.004199          0.000776             0.003598   
2026-01-16            0.022691         -0.004155             0.001915   
2026-01-19           -0.002616          0.008560            -0.000938   
2026-01-20           -0.017199          0.004684             0.002050   

           Dealer_Opt_Signal_a US_bond_5y  SkewSlope_a  SkewSlope  \
date                                                                
2010-01-04                 NaN       2.65          NaN  -0.082682   
2010-01-05                 NaN       2.56          NaN  -0.063613   
2010-01-06                 NaN       2.60          NaN  -0.072810   
2010-01-07                 NaN       2.62          NaN  -0.105570   
2010-01-08                 NaN       2.57          NaN  -0.077477   
...                        ...        ...          ...        ...   
2026-01-14            0.052200       3.72    -0.447106  -0.412201   
2026-01-15           -0.013482       3.77    -0.185785  -0.289951   
2026-01-16            0.018219       3.82    -0.373629  -0.385877   
2026-01-19           -0.107258        NaN    -0.347393  -0.520471   
2026-01-20           -0.151642       3.86    -0.644717  -0.678315   

            SkewSlope3_a  SkewSlope3  
date                                  
2010-01-04           NaN   -0.000068  
2010-01-05           NaN   -0

In [127]:
analyzer.indicator_option_iv(trading_session='day')

### 外資部位

In [28]:
# 抓取日盤 (Position)
raw_day = fm.option_institution_position('TXO', start_date=START, end_date=END)
raw_day.reset_index(drop=False, inplace=True)
# 抓取夜盤 (Aftermarket)
raw_night = fm.option_institution_aftermarket('TXO', start_date=START, end_date=END)
raw_night.reset_index(drop=False, inplace=True)

# 1. 處理函數 (加入容錯與標準化)
def get_signal_df(raw_df):
    if raw_df.empty:
        return pd.DataFrame()
        
    df_temp = raw_df.copy()
    
    # ----------------------------------------------------
    # [關鍵修正] 標準化 Call/Put 欄位
    # 如果看到中文，就轉成英文，讓後面邏輯統一
    # ----------------------------------------------------
    cp_map = {'買權': 'CALL', '賣權': 'PUT', 'Call': 'CALL', 'Put': 'PUT'}
    # 如果原本就是 CALL/PUT 也不會壞，因為 map 不到的會變成 NaN，所以要用 replace 或者先判斷
    if df_temp['call_put'].iloc[0] in ['買權', '賣權']:
        df_temp['call_put'] = df_temp['call_put'].map(cp_map)
    
    # 計算淨額與總額 (日盤也有 deal_amount 欄位，所以這行通用)
    df_temp['net_amt'] = df_temp['long_deal_amount'] - df_temp['short_deal_amount']
    df_temp['total_turnover'] = df_temp['long_deal_amount'] + df_temp['short_deal_amount']
    
    # Pivot (現在 call_put 已經統一為英文了)
    pivot_df = df_temp.pivot_table(
        index='date', 
        columns=['institutional_investors', 'call_put'], 
        values=['net_amt', 'total_turnover'],
        aggfunc='sum'
    )
    
    # 計算公式 (跟之前一樣)
    def _calc(df, inst):
        try:
            # 這裡我們只抓 CALL 和 PUT (因為已經轉成英文了)
            num = df[('net_amt', inst, 'CALL')] - df[('net_amt', inst, 'PUT')]
            den = (df[('total_turnover', inst, 'CALL')] + df[('total_turnover', inst, 'PUT')]).replace(0, 1)
            return num / den
        except KeyError:
            return pd.Series(dtype=float)

    res = pd.DataFrame(index=pivot_df.index)
    res['Foreign_Opt_Signal'] = _calc(pivot_df, '外資')
    res['Dealer_Opt_Signal'] = _calc(pivot_df, '自營商')
    
    return res

# ---------------------------------------------------------
# 以下呼叫方式不用變
# ---------------------------------------------------------

# [日盤] (裡面有 '買權'/'賣權') -> 函數會自動轉成 CALL/PUT
df_signal_day = get_signal_df(raw_day)

# [夜盤] (裡面只有 'CALL'/'PUT') -> 函數不做事，維持原樣
df_signal_night = get_signal_df(raw_night)
df_signal_night.columns = [f"{col}_a" for col in df_signal_night.columns]

# 合併
temp_df = pd.merge(df_signal_day, df_signal_night, left_index=True, right_index=True, how='outer')

df = analyzer.display_df()
df.index = pd.to_datetime(df.index, format='%Y-%m-%d')
temp_df.index = pd.to_datetime(temp_df.index, format='%Y-%m-%d')
df = df.merge(temp_df, left_index=True, right_index=True, how='left')
analyzer.update_df(df)

2026-02-04 19:17:56.579 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanOptionInstitutionalInvestors, data_id: TXO
2026-02-04 19:17:57.523 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanOptionInstitutionalInvestorsAfterHours, data_id: TXO


futures_id contract_date monthly_group     Open     High      Low  \
2010-01-04         TX        201001    2010-01-20   8203.0   8211.0   8101.0   
2010-01-05         TX        201001    2010-01-20   8212.0   8260.0   8125.0   
2010-01-06         TX        201001    2010-01-20   8197.0   8336.0   8179.0   
2010-01-07         TX        201001    2010-01-20   8335.0   8355.0   8230.0   
2010-01-08         TX        201001    2010-01-20   8287.0   8297.0   8183.0   
...               ...           ...           ...      ...      ...      ...   
2026-01-14         TX        202601    2026-01-21  31000.0  31162.0  30937.0   
2026-01-15         TX        202601    2026-01-21  30831.0  31057.0  30744.0   
2026-01-16         TX        202601    2026-01-21  31382.0  31536.0  31157.0   
2026-01-19         TX        202601    2026-01-21  31272.0  31774.0  31208.0   
2026-01-20         TX        202601    2026-01-21  31481.0  31742.0  31328.0   

              Close  spread  spread_per    Volume  ...  daily_pnl  \
2010-01-04   8166.0   -35.0       -0.43   84131.0  ...      -37.0   
2010-01-05   8178.0    11.0        0.13  108012.0  ...      -34.0   
2010-01-06   8320.0   142.0        1.74  120081.0  ...      123.0   
2010-01-07   8259.0   -62.0       -0.75  120555.0  ...      -76.0   
2010-01-08   8278.0    18.0        0.22  104771.0  ...       -9.0   
...             ...     ...         ...       ...  ...        ...   
2026-01-14  30982.0   112.0        0.36   54974.0  ...      -18.0   
2026-01-15  31050.0    70.0        0.23   58154.0  ...      219.0   
2026-01-16  31474.0   424.0        1.37   72871.0  ...       92.0   
2026-01-19  31669.0   193.0        0.61   89177.0  ...      397.0   
2026-01-20  31672.0     0.0        0.00   81251.0  ...      191.0   

            cum_daily_pnl daily_ret_a cum_daily_ret_a daily_pnl_a  \
2010-01-04          -37.0         NaN             NaN         NaN   
2010-01-05          -71.0         NaN             NaN         NaN   
2010-01-06           52.0         NaN             NaN         NaN   
2010-01-07          -24.0         NaN             NaN         NaN   
2010-01-08          -33.0         NaN             NaN         NaN   
...                   ...         ...             ...         ...   
2026-01-14         2122.0    0.002786        0.995384        86.0   
2026-01-15         2341.0   -0.003200        0.992184       -99.0   
2026-01-16         2433.0    0.004907        0.997091       153.0   
2026-01-19         2830.0   -0.004732        0.992359      -149.0   
2026-01-20         3021.0   -0.002623        0.989736       -83.0   

           cum_daily_pnl_a  Foreign_Opt_Signal  Dealer_Opt_Signal  \
2010-01-04             NaN                 NaN                NaN   
2010-01-05             NaN                 NaN                NaN   
2010-01-06             NaN                 NaN                NaN   
2010-01-07             NaN                 NaN                NaN   
2010-01-08             NaN                 NaN                NaN   
...                    ...                 ...                ...   
2026-01-14         14812.0            0.009633          -0.012854   
2026-01-15         14713.0            0.004199           0.000776   
2026-01-16         14866.0            0.022691          -0.004155   
2026-01-19         14717.0           -0.002616           0.008560   
2026-01-20         14634.0           -0.017199           0.004684   

            Foreign_Opt_Signal_a  Dealer_Opt_Signal_a  
2010-01-04                   NaN                  NaN  
2010-01-05                   NaN                  NaN  
2010-01-06                   NaN                  NaN  
2010-01-07                   NaN                  NaN  
2010-01-08                   NaN                  NaN  
...                          ...                  ...  
2026-01-14              0.006912             0.052200  
2026-01-15              0.003598            -0.013482  
2026-01-16              0.001915             0.018219  
202

In [81]:
analyzer.indicator_opt_position(indicator='Foreign_Opt_Signal', trading_session='day', sub_analysis=False)
analyzer.indicator_opt_position(indicator='Foreign_Opt_Signal', trading_session='day', sub_analysis=True)

In [ ]:
analyzer.indicator_opt_position(indicator='Foreign_Opt_Signal', trading_session='night', sub_analysis=False)

In [67]:
analyzer.indicator_opt_position(indicator='Foreign_Opt_Signal', trading_session='night', sub_analysis=False, time_series_analysis=True)

## 外資買賣

In [11]:
df_inst = pd.read_csv('../../../data/整體市場三大法人買賣表.csv')

df_inst['日期'] = pd.to_datetime(df_inst['日期'])
df_inst['Net'] = df_inst['買進'] - df_inst['賣出']
df_inst.rename(columns={'買進': 'buy', '賣出': 'sell'}, inplace=True)
pivot_df = df_inst.pivot(index='日期', columns='種類', values=['buy', 'sell', 'Net'])
pivot_df.columns = [f"{col[0]}_{col[1]}" for col in pivot_df.columns]

temp_df = analyzer.display_df()
temp_df = temp_df.merge(pivot_df, left_index=True, right_index=True, how='left')
analyzer.update_df(temp_df)

futures_id contract_date monthly_group     Open     High      Low  \
date                                                                           
2020-01-02         TX        202001    2020-01-15  12044.0  12120.0  12023.0   
2020-01-03         TX        202001    2020-01-15  12180.0  12198.0  11996.0   
2020-01-06         TX        202001    2020-01-15  12017.0  12034.0  11948.0   
2020-01-07         TX        202001    2020-01-15  11995.0  12009.0  11816.0   
2020-01-08         TX        202001    2020-01-15  11728.0  11892.0  11697.0   
...               ...           ...           ...      ...      ...      ...   
2026-01-14         TX        202601    2026-01-21  31000.0  31162.0  30937.0   
2026-01-15         TX        202601    2026-01-21  30831.0  31057.0  30744.0   
2026-01-16         TX        202601    2026-01-21  31382.0  31536.0  31157.0   
2026-01-19         TX        202601    2026-01-21  31272.0  31774.0  31208.0   
2026-01-20         TX        202601    2026-01-21  31481.0  31742.0  31328.0   

              Close  spread  spread_per    Volume  ...  \
date                                               ...   
2020-01-02  12102.0   108.0        0.90  100401.0  ...   
2020-01-03  12086.0   -15.0       -0.12  172660.0  ...   
2020-01-06  11950.0  -137.0       -1.13  118380.0  ...   
2020-01-07  11871.0   -78.0       -0.65  157264.0  ...   
2020-01-08  11788.0   -83.0       -0.70  158971.0  ...   
...             ...     ...         ...       ...  ...   
2026-01-14  30982.0   112.0        0.36   54974.0  ...   
2026-01-15  31050.0    70.0        0.23   58154.0  ...   
2026-01-16  31474.0   424.0        1.37   72871.0  ...   
2026-01-19  31669.0   193.0        0.61   89177.0  ...   
2026-01-20  31672.0     0.0        0.00   81251.0  ...   

            sell_Foreign_Dealer_Self  sell_Foreign_Investor  \
date                                                          
2020-01-02                12604610.0           2.825961e+10   
2020-01-03                12140490.0           3.747450e+10   
2020-01-06                 8498430.0           3.741593e+10   
2020-01-07                 8676200.0           4.532241e+10   
2020-01-08                 7482080.0           3.842789e+10   
...                              ...                    ...   
2026-01-14                       0.0           2.143468e+11   
2026-01-15                       0.0           2.265881e+11   
2026-01-16                       0.0           2.398726e+11   
2026-01-19                       0.0           2.554994e+11   
2026-01-20                       0.0           2.615255e+11   

           sell_Investment_Trust    sell_total Net_Dealer_Hedging  \
date                                                                
2020-01-02          2.184135e+09  3.615252e+10       2.376466e+09   
2020-01-03          2.398021e+09  5.089674e+10      -4.369021e+08   
2020-01-06          3.284215e+09  4.800463e+10       6.568383e+08   
2020-01-07          2.851857e+09  5.695957e+10      -7.147001e+08   
2020-01-08          1.583485e+09  4.820975e+10      -2.958244e+08   
...                          ...           ...                ...   
2026-01-14          1.738227e+10  2.605514e+11       6.188131e+09   
2026-01-15          1.510475e+10  2.756868e+11      -4.590572e+09   
2026-01-16          1.758191e+10  2.903068e+11       6.032128e+09   
2026-01-19          2.870183e+10  3.226821e+11      -4.092445e+09   
2026-01-20          2.138440e+10  3.168345e+11      -7.472637e+08   

           Net_Dealer_self  Net_Foreign_Dealer_Self  Net_Foreign_Investor  \
date                                                                        
2020-01-02    1.395424e+09               -2752060.0         -3.429870e+09   
2020-01-03   -5.680259e+08                3876970.0         -1.358661e+08   
2020-01-06   -9.574017e+08                 865550.0         -9.750910e+09   
2020-01-07   -1.225375e+09                 204180.0         -9.820883e+09   
2020-01-08   -5.279640e+08         

In [12]:
analyzer.indicator_institutional_flow()

## `美國公債`

### 長債
    yield_shock = US_bond_5y - US_bond_5y.shift(20)
用來殺估值的，長債成本快速上升會殺死需要藉很多錢的成長股，又或是未來 cash flow 折現回來不值錢  
yield_shock 超過 0.15 就不做多，甚至做空

    yield_divergence = (US_bond_5y / 30ma_5y) - 1
用來看現在 5y 利率是否偏離過去平均太多  
yield_divergence > 0.06 夜盤demean開始跌，日盤會再晚一點，大概0.1  
yield_divergence < -0.05 開始黑K

### 短債
    near_inversion = US_bond_6m - US_bond_3m
near_inversion > 0.3 快逃
代表市場現在很缺錢，救命

    near_yield_vol = US_bond_3m.rolling(20).std()
near_yield_vol < 0.013 都安全  
但超過 0.015 請開始做台股黑K，日盤跌爛

In [96]:
bond_5_year_df = fm.get_US_bond('United States 5-Year', START, END)

temp_df = analyzer.display_df()
temp_df.reset_index(inplace=True)
if 'index' in temp_df.columns:
    temp_df.rename(columns={'index': 'date'}, inplace=True)
temp_df['date'] = pd.to_datetime(temp_df['date'])

# Merge bonds with renaming to avoid duplicates
bond_map = {
    '5y': bond_5_year_df
}

for suffix, df in bond_map.items():
    # Extract only necessary columns and rename
    if 'value' in df.columns:
        sub_df = df[['date', 'value']].rename(columns={'value': f'US_bond_{suffix}'})
        temp_df = temp_df.merge(sub_df, on='date', how='left')
    else:
        # Fallback if columns are different, merge directly but be careful
        temp_df = temp_df.merge(df, on='date', how='left')

temp_df.set_index('date', inplace=True)

analyzer.update_df(temp_df)

2026-02-02 18:43:16.839 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.GovernmentBondsYield, data_id: United States 5-Year


futures_id contract_date monthly_group     Open     High      Low  \
date                                                                           
2010-01-04         TX        201001    2010-01-20   8203.0   8211.0   8101.0   
2010-01-05         TX        201001    2010-01-20   8212.0   8260.0   8125.0   
2010-01-06         TX        201001    2010-01-20   8197.0   8336.0   8179.0   
2010-01-07         TX        201001    2010-01-20   8335.0   8355.0   8230.0   
2010-01-08         TX        201001    2010-01-20   8287.0   8297.0   8183.0   
...               ...           ...           ...      ...      ...      ...   
2026-01-14         TX        202601    2026-01-21  31000.0  31162.0  30937.0   
2026-01-15         TX        202601    2026-01-21  30831.0  31057.0  30744.0   
2026-01-16         TX        202601    2026-01-21  31382.0  31536.0  31157.0   
2026-01-19         TX        202601    2026-01-21  31272.0  31774.0  31208.0   
2026-01-20         TX        202601    2026-01-21  31481.0  31742.0  31328.0   

              Close  spread  spread_per    Volume  ...  cum_daily_pnl  \
date                                               ...                  
2010-01-04   8166.0   -35.0       -0.43   84131.0  ...          -37.0   
2010-01-05   8178.0    11.0        0.13  108012.0  ...          -71.0   
2010-01-06   8320.0   142.0        1.74  120081.0  ...           52.0   
2010-01-07   8259.0   -62.0       -0.75  120555.0  ...          -24.0   
2010-01-08   8278.0    18.0        0.22  104771.0  ...          -33.0   
...             ...     ...         ...       ...  ...            ...   
2026-01-14  30982.0   112.0        0.36   54974.0  ...         2122.0   
2026-01-15  31050.0    70.0        0.23   58154.0  ...         2341.0   
2026-01-16  31474.0   424.0        1.37   72871.0  ...         2433.0   
2026-01-19  31669.0   193.0        0.61   89177.0  ...         2830.0   
2026-01-20  31672.0     0.0        0.00   81251.0  ...         3021.0   

            daily_ret_a cum_daily_ret_a daily_pnl_a cum_daily_pnl_a  \
date                                                                  
2010-01-04          NaN             NaN         NaN             NaN   
2010-01-05          NaN             NaN         NaN             NaN   
2010-01-06          NaN             NaN         NaN             NaN   
2010-01-07          NaN             NaN         NaN             NaN   
2010-01-08          NaN             NaN         NaN             NaN   
...                 ...             ...         ...             ...   
2026-01-14     0.002786        0.995384        86.0         14812.0   
2026-01-15    -0.003200        0.992184       -99.0         14713.0   
2026-01-16     0.004907        0.997091       153.0         14866.0   
2026-01-19    -0.004732        0.992359      -149.0         14717.0   
2026-01-20    -0.002623        0.989736       -83.0         14634.0   

           Foreign_Opt_Signal  Dealer_Opt_Signal  Foreign_Opt_Signal_a  \
date                                                                     
2010-01-04                NaN                NaN                   NaN   
2010-01-05                NaN                NaN                   NaN   
2010-01-06                NaN                NaN                   NaN   
2010-01-07                NaN                NaN                   NaN   
2010-01-08                NaN                NaN                   NaN   
...                       ...                ...                   ...   
2026-01-14           0.009633          -0.012854              0.006912   
2026-01-15           0.004199           0.000776              0.003598   
2026-01-16           0.022691          -0.004155              0.001915   
2026-01-19          -0.002616           0.008560             -0.000938   
2026-01-20          -0.017199           0.004684              0.002050   

            Dealer_Opt_Signal_a  US_bond_5y  
date                                         
2010-01-04                  NaN        2.

### long term

In [12]:
analyzer.indicator_US_bond(indicator='yield_shock')
# analyzer.indicator_US_bond(indicator='yield_divergence')
# analyzer.indicator_US_bond(indicator='yield_presure')

### short term

In [15]:
analyzer.indicator_US_bond(indicator='cash_crunch')
analyzer.indicator_US_bond(indicator='near_inversion')
analyzer.indicator_US_bond(indicator='near_yield_vol')

## 外匯

In [144]:
usd_twd = fm.get_exchange(currency="USD", start_date=START, end_date=END)
usd_twd['date'] = pd.to_datetime(usd_twd['date'])
usd_twd.set_index('date', inplace=True)
df = analyzer.display_df()
df = df.merge(usd_twd, left_index=True, right_index=True, how='left')

2026-02-02 21:49:24.896 | INFO     | FinMind.data.finmind_api:get_data:171 - download Dataset.TaiwanExchangeRate, data_id: USD


In [145]:
df

futures_id contract_date monthly_group     Open     High      Low  \
date                                                                           
2010-01-04         TX        201001    2010-01-20   8203.0   8211.0   8101.0   
2010-01-05         TX        201001    2010-01-20   8212.0   8260.0   8125.0   
2010-01-06         TX        201001    2010-01-20   8197.0   8336.0   8179.0   
2010-01-07         TX        201001    2010-01-20   8335.0   8355.0   8230.0   
2010-01-08         TX        201001    2010-01-20   8287.0   8297.0   8183.0   
...               ...           ...           ...      ...      ...      ...   
2026-01-14         TX        202601    2026-01-21  31000.0  31162.0  30937.0   
2026-01-15         TX        202601    2026-01-21  30831.0  31057.0  30744.0   
2026-01-16         TX        202601    2026-01-21  31382.0  31536.0  31157.0   
2026-01-19         TX        202601    2026-01-21  31272.0  31774.0  31208.0   
2026-01-20         TX        202601    2026-01-21  31481.0  31742.0  31328.0   

              Close  spread  spread_per    Volume  ...  US_bond_5y  \
date                                               ...               
2010-01-04   8166.0   -35.0       -0.43   84131.0  ...        2.65   
2010-01-05   8178.0    11.0        0.13  108012.0  ...        2.56   
2010-01-06   8320.0   142.0        1.74  120081.0  ...        2.60   
2010-01-07   8259.0   -62.0       -0.75  120555.0  ...        2.62   
2010-01-08   8278.0    18.0        0.22  104771.0  ...        2.57   
...             ...     ...         ...       ...  ...         ...   
2026-01-14  30982.0   112.0        0.36   54974.0  ...        3.72   
2026-01-15  31050.0    70.0        0.23   58154.0  ...        3.77   
2026-01-16  31474.0   424.0        1.37   72871.0  ...        3.82   
2026-01-19  31669.0   193.0        0.61   89177.0  ...         NaN   
2026-01-20  31672.0     0.0        0.00   81251.0  ...        3.86   

            SkewSlope_a SkewSlope SkewSlope3_a SkewSlope3 currency  cash_buy  \
date                                                                           
2010-01-04          NaN -0.082682          NaN  -0.000068      USD    31.470   
2010-01-05          NaN -0.063613          NaN  -0.000104      USD    31.505   
2010-01-06          NaN -0.072810          NaN  -0.000051      USD    31.520   
2010-01-07          NaN -0.105570          NaN  -0.000405      USD    31.520   
2010-01-08          NaN -0.077477          NaN  -0.000058      USD    31.525   
...                 ...       ...          ...        ...      ...       ...   
2026-01-14    -0.447106 -0.412201    -0.003909  -0.003667      USD    31.230   
2026-01-15    -0.185785 -0.289951    -0.000363  -0.001697      USD    31.175   
2026-01-16    -0.373629 -0.385877    -0.001636  -0.004780      USD    31.160   
2026-01-19    -0.347393 -0.520471    -0.004776  -0.032241      USD    31.195   
2026-01-20    -0.644717 -0.678315    -0.067403  -0.078003      USD    31.205   

            cash_sell  spot_buy  spot_sell  
date                                        
2010-01-04     32.012    31.770     31.870  
2010-01-05     32.047    31.805     31.905  
2010-01-06     32.062    31.820     31.920  
2010-01-07     32.062    31.820     31.920  
2010-01-08     32.067    31.825     31.925  
...               ...       ...        ...  
2026-01-14     31.900    31.580     31.680  
2026-01-15     31.845    31.525     31.625  
2026-01-16     31.830    31.510     31.610  
2026-01-19     31.865    31.545     31.645  
2026-01-20     31.875    31.555     31.655  

[3943 rows x 48 columns]

# backtest

In [80]:
analyzer.backtest(point_version=False)

=== Performance Metrics (Percentage) ===


d:\Github\Quant\projects\workStrategy\TX\analyzer.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

d:\Github\Quant\projects\workStrategy\TX\analyzer.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Total Return    CAGR Volatility Sharpe Max Drawdown Max DD Duration  \
Strategy       426.06%  34.77%     15.20%   2.29      -13.03%         74 days   
Benchmark      142.19%  17.23%     17.15%   1.00      -24.56%        344 days   

          Profit Factor Win Rate  Odds Avg Win Avg Loss Avg Return (Exp) Kelly  
Strategy           1.45   57.39%  1.07   0.72%   -0.68%            0.13%  0.17  
Benchmark          1.19   54.42%  0.99   0.79%   -0.80%            0.07%  0.08

In [247]:
# 假設你已經建立 analyzer 實例
# running_window 預設為 126 天 (半年)，你可以自訂例如 60 或 252
analyzer.show_performance_distributions(rolling_window=126)

Calculating rolling metrics for 1992 windows...


Rolling Metrics: 100%|██████████| 1992/1992 [00:03<00:00, 619.17it/s]


=== Rolling Performance Statistics (Window: 126 days) ===


CAGR   Volatility       Sharpe  Max Drawdown  Max DD Duration  \
count  1992.000000  1992.000000  1992.000000   1992.000000      1992.000000   
mean      0.213696     0.115666     1.792676     -0.068545        53.808233   
std       0.203418     0.042716     1.736042      0.041487        29.971196   
min      -0.203668     0.052844    -1.369957     -0.173707        13.000000   
25%       0.035882     0.084346     0.397352     -0.086821        30.000000   
50%       0.215737     0.105091     1.667839     -0.058722        44.000000   
75%       0.346359     0.133090     2.962862     -0.035900        73.000000   
max       1.109928     0.211619     8.225219     -0.019605       125.000000   

       Profit Factor     Win Rate         Odds        Kelly      Avg Win  \
count    1992.000000  1992.000000  1992.000000  1992.000000  1992.000000   
mean        1.400334     0.571417     1.039595     0.136695     0.006050   
std         0.392780     0.045978     0.262701     0.122673     0.002140   
min         0.738975     0.440476     0.567362    -0.195588     0.002269   
25%         1.088749     0.541257     0.834187     0.043234     0.004276   
50%         1.347668     0.573842     1.020262     0.143390     0.005856   
75%         1.619414     0.602068     1.183553     0.226082     0.007503   
max         2.651840     0.703125     1.995594     0.407483     0.011203   

          Avg Loss  Avg Return (Exp)  
count  1992.000000       1992.000000  
mean     -0.005877          0.000929  
std       0.001732          0.000807  
min      -0.011158         -0.000895  
25%      -0.006762          0.000198  
50%      -0.005700          0.001007  
75%      -0.004680          0.001515  
max      -0.002611          0.003102